In [5]:
# ===================================================================
# CÉLULA ÚNICA: Instalação + Código de Anonimização
# ===================================================================

# ETAPA 1: Instalações (Execute esta parte primeiro)
# -------------------------------------------------
print("Iniciando instalações...")
!pip install presidio-analyzer presidio-anonymizer spacy
!python -m spacy download pt_core_news_lg
print("Instalações concluídas.")
print("\n*** IMPORTANTE: REINICIE O AMBIENTE DE EXECUÇÃO AGORA! ***")
print("(Vá em 'Ambiente de execução' -> 'Reiniciar ambiente de execução' ou 'Kernel' -> 'Restart')")
print("Depois de reiniciar, execute esta célula NOVAMENTE.")

# -------------------------------------------------
# ETAPA 2: Código Principal (Execute APÓS reiniciar o ambiente)
# -------------------------------------------------
# (Só execute esta parte da célula DEPOIS de ter reiniciado o ambiente)

# Coloque um 'try...except' ou verifique se uma biblioteca chave já foi importada
# para evitar que a parte de instalação execute desnecessariamente em execuções futuras.
# Uma forma simples é tentar importar algo; se falhar, assumimos que é a primeira vez
# pós-restart e continuamos. Se funcionar, as instalações já foram feitas.
_ambiente_pronto = False
try:
    from presidio_analyzer import AnalyzerEngine
    _ambiente_pronto = True
    print("\nBibliotecas já carregadas, pulando para o código principal.")
except ModuleNotFoundError:
    print("\nERRO: Parece que o ambiente não foi reiniciado após a instalação.")
    print("Por favor, reinicie o ambiente e execute esta célula novamente.")
    # Você pode querer parar a execução aqui se o ambiente não estiver pronto
    # raise Exception("Reinicie o ambiente antes de continuar.") # Descomente para forçar a parada


if _ambiente_pronto:
    print("\nImportando bibliotecas...")
    from presidio_analyzer import AnalyzerEngine, PatternRecognizer, Pattern
    from presidio_anonymizer import AnonymizerEngine
    from presidio_anonymizer.entities import OperatorConfig
    # A importação específica do NlpEngineProvider também deve estar aqui
    from presidio_analyzer.nlp_engine import NlpEngineProvider
    print("Importações concluídas.")

    # --- Opcional: Reconhecedores Customizados ---
    # ...

    # 1. Inicializar o Motor de Análise (Analyzer)
    print("Inicializando o Analyzer Engine...")
    try:
        nlp_config = {
             "nlp_engine_name": "spacy",
             "models": [{"lang_code": "pt", "model_name": "pt_core_news_lg"}]
        }
        provider = NlpEngineProvider(nlp_configuration=nlp_config)
        nlp_engine_pt = provider.create_engine()

        analyzer = AnalyzerEngine(
            nlp_engine=nlp_engine_pt,
            supported_languages=['pt']
        )
        print("Analyzer Engine inicializado com sucesso para Português.")

    except Exception as e:
        print(f"ERRO ao inicializar AnalyzerEngine: {e}")
        print("Verifique se o modelo 'pt_core_news_lg' foi baixado e se o ambiente foi reiniciado.")
        raise

    # 2. Inicializar o Motor de Anonimização (Anonymizer)
    print("Inicializando o Anonymizer Engine...")
    anonymizer = AnonymizerEngine()

    # 3. Texto de Exemplo
    texto_para_anonimizar = """
    Prezados,
    Meu nome é Maria Clara Santos e meu CPF é 111.222.333-44.
    Resido na Rua das Palmeiras, nº 789, Bairro da Paz, Cidade Feliz - CF.
    Meu telefone de contato é +55 (81) 98765-1234 e o email para retorno é mariaclara.santos.teste@dominioficticio.com.
    Gostaria de relatar um problema com meu pedido nº 987654321. Falei com o atendente João Pedro.
    Meu cartão VISA terminado em 5555 foi usado na compra. O RG dela é 11.223.344-5.
    """

    print("\n--- Texto Original ---")
    print(texto_para_anonimizar)

    # 4. Analisar o texto para encontrar PII
    print("\nAnalisando o texto para encontrar PII (Idioma: pt)...")
    try:
        resultados_da_analise = analyzer.analyze(text=texto_para_anonimizar, language='pt')
        print(f"Encontradas {len(resultados_da_analise)} PII potenciais.")

        print("\n--- Detalhes das PII Encontradas ---")
        if resultados_da_analise:
            for i, resultado in enumerate(resultados_da_analise):
                start, end = resultado.start, resultado.end
                texto_detectado = texto_para_anonimizar[start:end].replace('\n', ' ')
                print(f"{i+1}. Tipo: {resultado.entity_type}, Texto: '{texto_detectado}', Score: {resultado.score:.2f}, Pos: ({start}, {end})")
        else:
            print("Nenhuma PII detectada.")

    except Exception as e:
        print(f"\nERRO DURANTE A ANÁLISE: {e}")
        resultados_da_analise = []

    # 5. Definir as Regras de Anonimização (Operadores)
    print("\nDefinindo regras de anonimização (Operadores)...")
    regras_de_anonimizacao = {
        "DEFAULT": OperatorConfig("replace", {"new_value": "<OCULTO>"}),
        "PERSON": OperatorConfig("replace", {"new_value": "<NOME>"}),
        "PHONE_NUMBER": OperatorConfig("mask", {"type": "mask", "masking_char": "*", "chars_to_mask": 8, "from_end": True}),
        "EMAIL_ADDRESS": OperatorConfig("replace", {"new_value": "<EMAIL>"}),
        "LOCATION": OperatorConfig("replace", {"new_value": "<ENDERECO>"}),
        "DATE_TIME": OperatorConfig("replace", {"new_value": "<DATA>"}),
        "NRP": OperatorConfig("replace", {"new_value": "<NUMERO_ID>"}), # Pega números como CPF, RG, Pedido
        "CREDIT_CARD": OperatorConfig("mask", {"type": "mask", "masking_char": "*", "chars_to_mask": 12, "from_end": False}),
        "ID": OperatorConfig("replace", {"new_value": "<DOCUMENTO>"}),
        "ID_NUMBER": OperatorConfig("replace", {"new_value": "<DOCUMENTO>"}),
    }

    # 6. Executar a Anonimização
    print("Executando a anonimização...")
    if resultados_da_analise:
        try:
            resultado_anonimizado = anonymizer.anonymize(
                text=texto_para_anonimizar,
                analyzer_results=resultados_da_analise,
                operators=regras_de_anonimizacao
            )

            print("\n--- Texto Anonimizado ---")
            print(resultado_anonimizado.text)

        except Exception as e:
            print(f"\nERRO DURANTE A ANONIMIZAÇÃO: {e}")
    else:
        print("\nNenhuma PII foi detectada ou a análise falhou, texto permanece original.")

    print("\n\nProcesso concluído!")

Iniciando instalações...
  Using cached https://github.com/explosion/spacy-models/releases/download/pt_core_news_lg-3.8.0/pt_core_news_lg-3.8.0-py3-none-any.whl (568.2 MB)
✔ Download and installation successful
You can now load the package via spacy.load('pt_core_news_lg')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


Instalações concluídas.

*** IMPORTANTE: REINICIE O AMBIENTE DE EXECUÇÃO AGORA! ***
(Vá em 'Ambiente de execução' -> 'Reiniciar ambiente de execução' ou 'Kernel' -> 'Restart')
Depois de reiniciar, execute esta célula NOVAMENTE.

Bibliotecas já carregadas, pulando para o código principal.

Importando bibliotecas...
Importações concluídas.
Inicializando o Analyzer Engine...


Analyzer Engine inicializado com sucesso para Português.
Inicializando o Anonymizer Engine...

--- Texto Original ---

    Prezados,
    Meu nome é Maria Clara Santos e meu CPF é 111.222.333-44.
    Resido na Rua das Palmeiras, nº 789, Bairro da Paz, Cidade Feliz - CF.
    Meu telefone de contato é +55 (81) 98765-1234 e o email para retorno é mariaclara.santos.teste@dominioficticio.com.
    Gostaria de relatar um problema com meu pedido nº 987654321. Falei com o atendente João Pedro.
    Meu cartão VISA terminado em 5555 foi usado na compra. O RG dela é 11.223.344-5.
    

Analisando o texto para encontrar PII (Idioma: pt)...
Encontradas 12 PII potenciais.

--- Detalhes das PII Encontradas ---
1. Tipo: EMAIL_ADDRESS, Texto: 'mariaclara.santos.teste@dominioficticio.com', Score: 1.00, Pos: (227, 270)
2. Tipo: LOCATION, Texto: 'Prezados', Score: 0.85, Pos: (5, 13)
3. Tipo: PERSON, Texto: 'Maria Clara Santos', Score: 0.85, Pos: (30, 48)
4. Tipo: LOCATION, Texto: 'Rua das Palmeiras', Score:

In [4]:
# ===================================================================
# CÉLULA ÚNICA: Instalação + Código de Anonimização + Interface Gradio
# ===================================================================

# ETAPA 1: Instalações (Execute esta parte primeiro)
# -------------------------------------------------
print("Iniciando instalações...")
# Adicionado 'gradio' à lista de instalações
!pip install presidio-analyzer presidio-anonymizer spacy gradio
!python -m spacy download pt_core_news_lg
print("Instalações concluídas.")
print("\n*** IMPORTANTE: REINICIE O AMBIENTE DE EXECUÇÃO AGORA! ***")
print("(Vá em 'Ambiente de execução' -> 'Reiniciar ambiente de execução' ou 'Kernel' -> 'Restart')")
print("Depois de reiniciar, execute esta célula NOVAMENTE.")

# -------------------------------------------------
# ETAPA 2: Código Principal (Execute APÓS reiniciar o ambiente)
# -------------------------------------------------
# (Só execute esta parte da célula DEPOIS de ter reiniciado o ambiente)

_ambiente_pronto = False
try:
    # Tenta importar uma biblioteca chave de cada pacote principal
    from presidio_analyzer import AnalyzerEngine
    import spacy
    import gradio
    _ambiente_pronto = True
    print("\nBibliotecas já carregadas, pulando para o código principal.")
except ModuleNotFoundError:
    print("\nERRO: Parece que o ambiente não foi reiniciado após a instalação ou alguma instalação falhou.")
    print("Por favor, REINICIE O AMBIENTE e execute esta célula novamente.")
    # Descomente a linha abaixo para forçar a parada se o ambiente não estiver pronto
    # raise Exception("Reinicie o ambiente antes de continuar.")


if _ambiente_pronto:
    print("\nImportando bibliotecas...")
    # Presidio imports
    from presidio_analyzer import AnalyzerEngine, PatternRecognizer, Pattern
    from presidio_anonymizer import AnonymizerEngine
    from presidio_anonymizer.entities import OperatorConfig
    from presidio_analyzer.nlp_engine import NlpEngineProvider
    # Gradio import
    import gradio as gr
    print("Importações concluídas.")

    # --- Opcional: Reconhecedores Customizados ---
    # ... (Seu código de reconhecedores customizados iria aqui)

    # 1. Inicializar o Motor de Análise (Analyzer)
    print("Inicializando o Analyzer Engine...")
    try:
        nlp_config = {
             "nlp_engine_name": "spacy",
             "models": [{"lang_code": "pt", "model_name": "pt_core_news_lg"}]
        }
        provider = NlpEngineProvider(nlp_configuration=nlp_config)
        nlp_engine_pt = provider.create_engine()

        analyzer = AnalyzerEngine(
            nlp_engine=nlp_engine_pt,
            supported_languages=['pt']
        )
        print("Analyzer Engine inicializado com sucesso para Português.")

    except Exception as e:
        print(f"ERRO CRÍTICO ao inicializar AnalyzerEngine: {e}")
        print("Verifique se o modelo 'pt_core_news_lg' foi baixado e se o ambiente foi reiniciado.")
        print("A interface Gradio não funcionará sem o Analyzer.")
        # Interrompe a execução se o Analyzer falhar
        raise SystemExit("Falha na inicialização do Analyzer Engine.") from e

    # 2. Inicializar o Motor de Anonimização (Anonymizer)
    print("Inicializando o Anonymizer Engine...")
    anonymizer = AnonymizerEngine()
    print("Anonymizer Engine inicializado com sucesso.")

    # 3. Definir as Regras de Anonimização (Operadores)
    #    Estas regras serão usadas pela função do Gradio
    print("Definindo regras de anonimização (Operadores)...")
    regras_de_anonimizacao = {
        "DEFAULT": OperatorConfig("replace", {"new_value": "<OCULTO>"}),
        "PERSON": OperatorConfig("replace", {"new_value": "<NOME>"}),
        "PHONE_NUMBER": OperatorConfig("mask", {"type": "mask", "masking_char": "*", "chars_to_mask": 8, "from_end": True}),
        "EMAIL_ADDRESS": OperatorConfig("replace", {"new_value": "<EMAIL>"}),
        "LOCATION": OperatorConfig("replace", {"new_value": "<ENDERECO>"}),
        "DATE_TIME": OperatorConfig("replace", {"new_value": "<DATA>"}),
        "NRP": OperatorConfig("replace", {"new_value": "<NUMERO_ID>"}), # Pega números como CPF, RG, Pedido
        "CREDIT_CARD": OperatorConfig("mask", {"type": "mask", "masking_char": "*", "chars_to_mask": 12, "from_end": False}),
        # Adicionando tipos comuns que o modelo pt pode detectar
        "CPF": OperatorConfig("replace", {"new_value": "<CPF>"}),
        "CNPJ": OperatorConfig("replace", {"new_value": "<CNPJ>"}),
        "URL": OperatorConfig("replace", {"new_value": "<URL>"}),
        "AGE": OperatorConfig("replace", {"new_value": "<IDADE>"}),
        "ID": OperatorConfig("replace", {"new_value": "<DOCUMENTO>"}), # Genérico para IDs
        # Ajustando o default do spaCy para RG
        "BRAZIL_RG_NUMBER": OperatorConfig("replace", {"new_value": "<RG>"}),
    }
    print("Regras de anonimização definidas.")

    # 4. Função para processar o texto no Gradio
    #    Esta função usa os objetos 'analyzer', 'anonymizer' e 'regras_de_anonimizacao'
    #    que foram inicializados acima.
    def anonymize_text_gradio(text_input):
        """
        Analisa e anonimiza o texto de entrada usando Presidio.
        Retorna o texto anonimizado ou uma mensagem de erro/status.
        """
        if not text_input or not text_input.strip():
             return "Por favor, insira algum texto para anonimizar."

        print(f"\nRecebido texto para anonimizar via Gradio (Tamanho: {len(text_input)} chars).")
        try:
            print("Analisando texto...")
            resultados_da_analise = analyzer.analyze(text=text_input, language='pt')
            print(f"Análise concluída. Encontradas {len(resultados_da_analise)} PII potenciais.")

            if not resultados_da_analise:
                print("Nenhuma PII encontrada. Retornando texto original.")
                return "(Nenhuma PII detectada) \n\n" + text_input

            print("Executando anonimização...")
            resultado_anonimizado = anonymizer.anonymize(
                text=text_input,
                analyzer_results=resultados_da_analise,
                operators=regras_de_anonimizacao
            )
            print("Anonimização concluída.")
            return resultado_anonimizado.text

        except Exception as e:
            print(f"\nERRO DURANTE O PROCESSAMENTO GRADIO: {e}")
            # Retorna uma mensagem de erro para a interface Gradio
            return f"Ocorreu um erro durante o processamento: {e}"

    # 5. Configurar e Lançar a Interface Gradio
    print("\nConfigurando e iniciando a interface Gradio...")

    iface = gr.Interface(
        fn=anonymize_text_gradio,
        inputs=gr.Textbox(lines=15, placeholder="Cole ou digite o texto que você deseja anonimizar aqui...", label="Texto Original"),
        outputs=gr.Textbox(lines=15, label="Texto Anonimizado", interactive=False),
        title="Ferramenta de Anonimização de Texto (Presidio)",
        description="Cole um texto no campo 'Texto Original' e veja a versão anonimizada no campo 'Texto Anonimizado'. Usa o Presidio com o modelo de linguagem pt_core_news_lg para Português.",
        allow_flagging='never',
        theme=gr.themes.Soft() # Tente outros temas: Default(), Glass(), Monarch()
    )

    # Lança a interface. Em notebooks como Colab, use share=True para obter um link público.
    # Se estiver rodando localmente, share=False é geralmente suficiente.
    print("Lançando a interface Gradio. Aguarde o link ou a interface aparecer abaixo...")
    try:
        # Em ambientes como Google Colab/Kaggle, share=True é necessário para acessibilidade externa.
        # Se rodar localmente, pode usar share=False.
        # O debug=True pode ajudar a ver logs no console onde o script Python está rodando.
        iface.launch(share=True, debug=False)
        print("\nInterface Gradio ativa. Use o link acima ou a interface incorporada.")
        print("Pressione CTRL+C no terminal (se aplicável) para parar o servidor Gradio.")
    except Exception as e:
        print(f"ERRO ao lançar a interface Gradio: {e}")
        print("Verifique se a porta está disponível ou se há algum conflito.")

    print("\n\nFim do script (a interface Gradio pode continuar rodando).")

# Mensagem final caso o ambiente não esteja pronto
else:
    print("\nO código principal não foi executado porque o ambiente não parece estar pronto.")
    print("Certifique-se de ter executado a Etapa 1 (instalações) e REINICIADO o ambiente de execução antes de rodar a célula novamente.")

Iniciando instalações...
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 568.2/568.2 MB 3.6 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('pt_core_news_lg')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


Instalações concluídas.

*** IMPORTANTE: REINICIE O AMBIENTE DE EXECUÇÃO AGORA! ***
(Vá em 'Ambiente de execução' -> 'Reiniciar ambiente de execução' ou 'Kernel' -> 'Restart')
Depois de reiniciar, execute esta célula NOVAMENTE.

Bibliotecas já carregadas, pulando para o código principal.

Importando bibliotecas...
Importações concluídas.
Inicializando o Analyzer Engine...


/usr/local/lib/python3.11/dist-packages/gradio/interface.py:415: UserWarning: The `allow_flagging` parameter in `Interface` is deprecated.Use `flagging_mode` instead.
  warnings.warn(


Analyzer Engine inicializado com sucesso para Português.
Inicializando o Anonymizer Engine...
Anonymizer Engine inicializado com sucesso.
Definindo regras de anonimização (Operadores)...
Regras de anonimização definidas.

Configurando e iniciando a interface Gradio...
Lançando a interface Gradio. Aguarde o link ou a interface aparecer abaixo...
Colab notebook detected. To show errors in colab notebook, set debug=True in launch()
* Running on public URL: https://86222537bfbbf12acf.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)



Interface Gradio ativa. Use o link acima ou a interface incorporada.
Pressione CTRL+C no terminal (se aplicável) para parar o servidor Gradio.


Fim do script (a interface Gradio pode continuar rodando).
